In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [82]:
import pandas as pd 
import numpy as np 
import plotly.express as px 
from sklearn.metrics import r2_score 
from sklearn.model_selection import train_test_split
from sklearn import linear_model
import os
import opendatasets as od
import statsmodels.api as sm 

In [83]:
url = 'https://www.kaggle.com/datasets/aungpyaeap/supermarket-sales'

In [84]:
dataset = od.download(url)

Skipping, found downloaded files in ".\supermarket-sales" (use force=True to force download)


In [85]:
dir = '.\supermarket-sales'

In [86]:
filename = os.listdir(dir)
files = [file for file in filename]
file = files[0]

In [87]:
path = os.path.join(dir,file)

In [88]:
df= pd.read_csv(path)

In [89]:
df.columns

Index(['Invoice ID', 'Branch', 'City', 'Customer type', 'Gender',
       'Product line', 'Unit price', 'Quantity', 'Tax 5%', 'Total', 'Date',
       'Time', 'Payment', 'cogs', 'gross margin percentage', 'gross income',
       'Rating'],
      dtype='object')

In [90]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000 entries, 0 to 999
Data columns (total 17 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   Invoice ID               1000 non-null   object 
 1   Branch                   1000 non-null   object 
 2   City                     1000 non-null   object 
 3   Customer type            1000 non-null   object 
 4   Gender                   1000 non-null   object 
 5   Product line             1000 non-null   object 
 6   Unit price               1000 non-null   float64
 7   Quantity                 1000 non-null   int64  
 8   Tax 5%                   1000 non-null   float64
 9   Total                    1000 non-null   float64
 10  Date                     1000 non-null   object 
 11  Time                     1000 non-null   object 
 12  Payment                  1000 non-null   object 
 13  cogs                     1000 non-null   float64
 14  gross margin percentage  

In [91]:
df.describe()

Unit price     Quantity       Tax 5%        Total        cogs  \
count  1000.000000  1000.000000  1000.000000  1000.000000  1000.00000   
mean     55.672130     5.510000    15.379369   322.966749   307.58738   
std      26.494628     2.923431    11.708825   245.885335   234.17651   
min      10.080000     1.000000     0.508500    10.678500    10.17000   
25%      32.875000     3.000000     5.924875   124.422375   118.49750   
50%      55.230000     5.000000    12.088000   253.848000   241.76000   
75%      77.935000     8.000000    22.445250   471.350250   448.90500   
max      99.960000    10.000000    49.650000  1042.650000   993.00000   

       gross margin percentage  gross income      Rating  
count             1.000000e+03   1000.000000  1000.00000  
mean              4.761905e+00     15.379369     6.97270  
std               6.131498e-14     11.708825     1.71858  
min               4.761905e+00      0.508500     4.00000  
25%               4.761905e+00      5.924875     5.50000  
50%               4.761905e+00     12.088000     7.00000  
75%               4.761905e+00     22.445250     8.50000  
max               4.761905e+00     49.650000    10.00000

In [95]:
df['Date'] = pd.to_datetime(df['Date'])

In [96]:
df['day'] = df['Date'].dt.dayofweek
df['day']

0      5
1      4
2      6
3      6
4      4
5      0
6      0
7      6
8      3
9      2
10     2
11     5
12     1
13     3
14     4
15     1
16     0
17     1
18     0
19     0
20     0
21     1
22     4
23     6
24     5
25     4
26     4
27     6
28     4
29     4
30     0
31     0
32     3
33     4
34     2
35     0
36     6
37     1
38     5
39     6
40     3
41     5
42     4
43     0
44     5
45     5
46     2
47     2
48     6
49     1
50     6
51     6
52     4
53     4
54     3
55     3
56     2
57     3
58     6
59     1
60     4
61     6
62     6
63     2
64     3
65     2
66     6
67     0
68     3
69     5
70     6
71     0
72     1
73     5
74     1
75     6
76     2
77     5
78     1
79     1
80     0
81     5
82     2
83     5
84     5
85     1
86     0
87     2
88     2
89     2
90     2
91     5
92     3
93     1
94     2
95     4
96     4
97     5
98     5
99     1
100    1
101    4
102    4
103    3
104    1
105    5
106    5
107    4
108    6
109    6
110    1
1

In [94]:
df.columns

Index(['Invoice ID', 'Branch', 'City', 'Customer type', 'Gender',
       'Product line', 'Unit price', 'Quantity', 'Tax 5%', 'Total', 'Date',
       'Time', 'Payment', 'cogs', 'gross margin percentage', 'gross income',
       'Rating'],
      dtype='object')

In [98]:
date_mapping = {
    1: 'Monday',
    2: 'Tuesday',
    3: 'Wednesday',
    4: 'Thursday',
    5: 'Friday',
    6: 'Saturday',
    0: 'Sunday'
}

df['DayName'] = df['day'].map(date_mapping)
df['DayName']

0         Friday
1       Thursday
2       Saturday
3       Saturday
4       Thursday
5         Sunday
6         Sunday
7       Saturday
8      Wednesday
9        Tuesday
10       Tuesday
11        Friday
12        Monday
13     Wednesday
14      Thursday
15        Monday
16        Sunday
17        Monday
18        Sunday
19        Sunday
20        Sunday
21        Monday
22      Thursday
23      Saturday
24        Friday
25      Thursday
26      Thursday
27      Saturday
28      Thursday
29      Thursday
30        Sunday
31        Sunday
32     Wednesday
33      Thursday
34       Tuesday
35        Sunday
36      Saturday
37        Monday
38        Friday
39      Saturday
40     Wednesday
41        Friday
42      Thursday
43        Sunday
44        Friday
45        Friday
46       Tuesday
47       Tuesday
48      Saturday
49        Monday
50      Saturday
51      Saturday
52      Thursday
53      Thursday
54     Wednesday
55     Wednesday
56       Tuesday
57     Wednesday
58      Saturd

In [99]:
df['Month'] = df['Date'].dt.month
df['Month']

0      1
1      3
2      3
3      1
4      2
5      3
6      2
7      2
8      1
9      2
10     2
11     3
12     2
13     2
14     3
15     1
16     3
17     1
18     1
19     3
20     2
21     3
22     3
23     2
24     3
25     3
26     2
27     3
28     1
29     3
30     2
31     1
32     1
33     3
34     2
35     1
36     3
37     1
38     3
39     3
40     1
41     2
42     2
43     3
44     3
45     3
46     2
47     2
48     2
49     3
50     2
51     2
52     3
53     1
54     3
55     2
56     3
57     2
58     1
59     3
60     2
61     2
62     2
63     3
64     2
65     3
66     2
67     1
68     1
69     2
70     1
71     2
72     3
73     3
74     1
75     1
76     1
77     1
78     3
79     1
80     1
81     1
82     1
83     2
84     3
85     3
86     3
87     3
88     1
89     2
90     1
91     1
92     1
93     3
94     2
95     3
96     3
97     2
98     3
99     3
100    3
101    3
102    2
103    3
104    3
105    1
106    1
107    3
108    3
109    3
110    2
1

In [100]:
month_mapping = {
    1: 'January',
    2: 'February',
    3: 'March',
    4: 'April',
    5: 'May',
    6: 'June',
    7: 'July',
    8: 'August',
    9: 'September',
    10: 'October',
    11: 'November',
    12: 'December'
}
df['MonthName'] = df['Month'].map(month_mapping)
df['MonthName']

0       January
1         March
2         March
3       January
4      February
5         March
6      February
7      February
8       January
9      February
10     February
11        March
12     February
13     February
14        March
15      January
16        March
17      January
18      January
19        March
20     February
21        March
22        March
23     February
24        March
25        March
26     February
27        March
28      January
29        March
30     February
31      January
32      January
33        March
34     February
35      January
36        March
37      January
38        March
39        March
40      January
41     February
42     February
43        March
44        March
45        March
46     February
47     February
48     February
49        March
50     February
51     February
52        March
53      January
54        March
55     February
56        March
57     February
58      January
59        March
60     February
61     February
62     F

In [101]:
df.columns

Index(['Invoice ID', 'Branch', 'City', 'Customer type', 'Gender',
       'Product line', 'Unit price', 'Quantity', 'Tax 5%', 'Total', 'Date',
       'Time', 'Payment', 'cogs', 'gross margin percentage', 'gross income',
       'Rating', 'day', 'DayName', 'Month', 'MonthName'],
      dtype='object')

## Linear Regression Analysis 

In [102]:
data = df[['Invoice ID','Time','DayName', 'MonthName','Branch','City','Customer type','Gender', 'Product line','Unit price', 'Quantity', 'Tax 5%', 'Total', 'Payment','Rating','gross income']]
data

Invoice ID   Time    DayName MonthName Branch       City Customer type  \
0    750-67-8428  13:08     Friday   January      A     Yangon        Member   
1    226-31-3081  10:29   Thursday     March      C  Naypyitaw        Normal   
2    631-41-3108  13:23   Saturday     March      A     Yangon        Normal   
3    123-19-1176  20:33   Saturday   January      A     Yangon        Member   
4    373-73-7910  10:37   Thursday  February      A     Yangon        Normal   
5    699-14-3026  18:30     Sunday     March      C  Naypyitaw        Normal   
6    355-53-5943  14:36     Sunday  February      A     Yangon        Member   
7    315-22-5665  11:38   Saturday  February      C  Naypyitaw        Normal   
8    665-32-9167  17:15  Wednesday   January      A     Yangon        Member   
9    692-92-5582  13:27    Tuesday  February      B   Mandalay        Member   
10   351-62-0822  18:07    Tuesday  February      B   Mandalay        Member   
11   529-56-3974  17:03     Friday     March      B   Mandalay        Member   
12   365-64-0515  10:25     Monday  February      A     Yangon        Normal   
13   252-56-2699  16:48  Wednesday  February      A     Yangon        Normal   
14   829-34-3910  19:21   Thursday     March      A     Yangon        Normal   
15   299-46-1805  16:19     Monday   January      B   Mandalay        Member   
16   656-95-9349  11:03     Sunday     March      A     Yangon        Member   
17   765-26-6951  10:39     Monday   January      A     Yangon        Normal   
18   329-62-1586  18:00     Sunday   January      A     Yangon        Normal   
19   319-50-3348  15:30     Sunday     March      B   Mandalay        Normal   
20   300-71-4605  11:24     Sunday  February      C  Naypyitaw        Member   
21   371-85-5789  10:40     Monday     March      B   Mandalay        Normal   
22   273-16-6619  12:20   Thursday     March      B   Mandalay        Normal   
23   636-48-8204  11:15   Saturday  February      A     Yangon        Normal   
24   549-59-1358  17:36     Friday     March      A     Yangon        Member   
25   227-03-5010  19:20   Thursday     March      A     Yangon        Member   
26   649-29-6775  15:31   Thursday  February      B   Mandalay        Normal   
27   189-17-4241  12:17   Saturday     March      A     Yangon        Normal   
28   145-94-9061  19:48   Thursday   January      B   Mandalay        Normal   
29   848-62-7243  15:36   Thursday     March      A     Yangon        Normal   
30   871-79-8483  19:39     Sunday  February      B   Mandalay        Normal   
31   149-71-6266  12:43     Sunday   January      B   Mandalay        Member   
32   640-49-2076  14:49  Wednesday   January      B   Mandalay        Normal   
33   595-11-5460  10:12   Thursday     March      A     Yangon        Normal   
34   183-56-6882  10:42    Tuesday  February      C  Naypyitaw        Member   
35   232-16-2483  12:28     Sunday   January      C  Naypyitaw        Member   
36   129-29-8530  19:15   Saturday     March      A     Yangon        Member   
37   272-65-1806  17:17     Monday   January      A     Yangon        Normal   
38   333-73-7901  13:24     Friday     March      C  Naypyitaw        Normal   
39   777-82-7220  13:01   Saturday     March      B   Mandalay        Member   
40   280-35-5823  18:45  Wednesday   January      B   Mandalay        Member   
41   554-53-8700  10:11     Friday  February      C  Naypyitaw        Member   
42   354-25-5821  13:03   Thursday  February      B   Mandalay        Member   
43   228-96-1411  20:39     Sunday     March      C  Naypyitaw        Member   
44   617-15-4209  19:47     Friday     March      C  Naypyitaw        Member   
45   132-32-9879  18:00     Friday     March      B   Mandalay        Member   
46   370-41-7321  17:24    Tuesday  February      B   Mandalay        Member   
47   727-46-3608  15:47    Tuesday  February      B   Mandalay        Member   
48   669-54-1719  12:45   Saturday  February      B   Mandalay        Member   
49   5

In [103]:
data.fillna('Sunday')

Invoice ID   Time    DayName MonthName Branch       City Customer type  \
0    750-67-8428  13:08     Friday   January      A     Yangon        Member   
1    226-31-3081  10:29   Thursday     March      C  Naypyitaw        Normal   
2    631-41-3108  13:23   Saturday     March      A     Yangon        Normal   
3    123-19-1176  20:33   Saturday   January      A     Yangon        Member   
4    373-73-7910  10:37   Thursday  February      A     Yangon        Normal   
5    699-14-3026  18:30     Sunday     March      C  Naypyitaw        Normal   
6    355-53-5943  14:36     Sunday  February      A     Yangon        Member   
7    315-22-5665  11:38   Saturday  February      C  Naypyitaw        Normal   
8    665-32-9167  17:15  Wednesday   January      A     Yangon        Member   
9    692-92-5582  13:27    Tuesday  February      B   Mandalay        Member   
10   351-62-0822  18:07    Tuesday  February      B   Mandalay        Member   
11   529-56-3974  17:03     Friday     March      B   Mandalay        Member   
12   365-64-0515  10:25     Monday  February      A     Yangon        Normal   
13   252-56-2699  16:48  Wednesday  February      A     Yangon        Normal   
14   829-34-3910  19:21   Thursday     March      A     Yangon        Normal   
15   299-46-1805  16:19     Monday   January      B   Mandalay        Member   
16   656-95-9349  11:03     Sunday     March      A     Yangon        Member   
17   765-26-6951  10:39     Monday   January      A     Yangon        Normal   
18   329-62-1586  18:00     Sunday   January      A     Yangon        Normal   
19   319-50-3348  15:30     Sunday     March      B   Mandalay        Normal   
20   300-71-4605  11:24     Sunday  February      C  Naypyitaw        Member   
21   371-85-5789  10:40     Monday     March      B   Mandalay        Normal   
22   273-16-6619  12:20   Thursday     March      B   Mandalay        Normal   
23   636-48-8204  11:15   Saturday  February      A     Yangon        Normal   
24   549-59-1358  17:36     Friday     March      A     Yangon        Member   
25   227-03-5010  19:20   Thursday     March      A     Yangon        Member   
26   649-29-6775  15:31   Thursday  February      B   Mandalay        Normal   
27   189-17-4241  12:17   Saturday     March      A     Yangon        Normal   
28   145-94-9061  19:48   Thursday   January      B   Mandalay        Normal   
29   848-62-7243  15:36   Thursday     March      A     Yangon        Normal   
30   871-79-8483  19:39     Sunday  February      B   Mandalay        Normal   
31   149-71-6266  12:43     Sunday   January      B   Mandalay        Member   
32   640-49-2076  14:49  Wednesday   January      B   Mandalay        Normal   
33   595-11-5460  10:12   Thursday     March      A     Yangon        Normal   
34   183-56-6882  10:42    Tuesday  February      C  Naypyitaw        Member   
35   232-16-2483  12:28     Sunday   January      C  Naypyitaw        Member   
36   129-29-8530  19:15   Saturday     March      A     Yangon        Member   
37   272-65-1806  17:17     Monday   January      A     Yangon        Normal   
38   333-73-7901  13:24     Friday     March      C  Naypyitaw        Normal   
39   777-82-7220  13:01   Saturday     March      B   Mandalay        Member   
40   280-35-5823  18:45  Wednesday   January      B   Mandalay        Member   
41   554-53-8700  10:11     Friday  February      C  Naypyitaw        Member   
42   354-25-5821  13:03   Thursday  February      B   Mandalay        Member   
43   228-96-1411  20:39     Sunday     March      C  Naypyitaw        Member   
44   617-15-4209  19:47     Friday     March      C  Naypyitaw        Member   
45   132-32-9879  18:00     Friday     March      B   Mandalay        Member   
46   370-41-7321  17:24    Tuesday  February      B   Mandalay        Member   
47   727-46-3608  15:47    Tuesday  February      B   Mandalay        Member   
48   669-54-1719  12:45   Saturday  February      B   Mandalay        Member   
49   5

In [104]:
data.columns

Index(['Invoice ID', 'Time', 'DayName', 'MonthName', 'Branch', 'City',
       'Customer type', 'Gender', 'Product line', 'Unit price', 'Quantity',
       'Tax 5%', 'Total', 'Payment', 'Rating', 'gross income'],
      dtype='object')

In [105]:
pd.set_option('display.max_columns',None)

In [106]:
data2 = data.drop(columns=['Invoice ID','Time','Quantity'])

In [107]:
dummy = pd.get_dummies(data2).astype(int)
dummy

Unit price  Tax 5%  Total  Rating  gross income  DayName_Friday  \
0            74      26    548       9            26               1   
1            15       3     80       9             3               0   
2            46      16    340       7            16               0   
3            58      23    489       8            23               0   
4            86      30    634       5            30               0   
5            85      29    627       4            29               0   
6            68      20    433       5            20               0   
7            73      36    772       8            36               0   
8            36       3     76       7             3               0   
9            54       8    172       5             8               0   
10           14       2     60       4             2               0   
11           25       5    107       6             5               1   
12           46      11    246       7            11               0   
13           43      21    453       8            21               0   
14           71      35    749       5            35               0   
15           93      28    590       4            28               0   
16           68      24    506       4            24               0   
17           72      21    457       6            21               0   
18           54       8    172       8             8               0   
19           40       4     84       4             4               0   
20           86      21    451       4            21               0   
21           87      13    277       5            13               0   
22           33       3     69       4             3               0   
23           34       8    181       9             8               0   
24           88      13    279       6            13               1   
25           52      21    441       8            21               0   
26           33       1     35       6             1               0   
27           87       8    184       7             8               0   
28           88      22    463       9            22               0   
29           24      11    235       7            11               0   
30           94      23    494       4            23               0   
31           78      35    737       4            35               0   
32           83      33    703       5            33               0   
33           96       9    202       5             9               0   
34           99      19    417       7            19               0   
35           68       3     71       6             3               0   
36           62      15    328       7            15               0   
37           60      27    575       4            27               0   
38           54      21    461       7            21               1   
39           30      12    253       7            12               0   
40           86       4     91       7             4               0   
41           56       5    117       6             5               1   
42           69      20    435       5            20               0   
43           98      39    829       7            39               0   
44           15       1     32       7             1               1   
45           93      18    394       9            18               1   
46           56      25    535       8            25               0   
47           20       9    189       4             9               0   
48           18       5    119       8             5               0   
49           82      41    867       7            41               0   
50           91      31    671       9            31               0   
51           44      11    234       8            11               0   
52           17       3     75       6             3               0   
53           15       0     16       6             0               0   
54           16       1     33       6       

In [108]:
pd.set_option('display.max_rows',None)

In [109]:
dummy.columns

Index(['Unit price', 'Tax 5%', 'Total', 'Rating', 'gross income',
       'DayName_Friday', 'DayName_Monday', 'DayName_Saturday',
       'DayName_Sunday', 'DayName_Thursday', 'DayName_Tuesday',
       'DayName_Wednesday', 'MonthName_February', 'MonthName_January',
       'MonthName_March', 'Branch_A', 'Branch_B', 'Branch_C', 'City_Mandalay',
       'City_Naypyitaw', 'City_Yangon', 'Customer type_Member',
       'Customer type_Normal', 'Gender_Female', 'Gender_Male',
       'Product line_Electronic accessories',
       'Product line_Fashion accessories', 'Product line_Food and beverages',
       'Product line_Health and beauty', 'Product line_Home and lifestyle',
       'Product line_Sports and travel', 'Payment_Cash', 'Payment_Credit card',
       'Payment_Ewallet'],
      dtype='object')

In [110]:
x= dummy.to_numpy()
x


array([[ 74,  26, 548, ...,   0,   0,   1],
       [ 15,   3,  80, ...,   1,   0,   0],
       [ 46,  16, 340, ...,   0,   1,   0],
       ...,
       [ 31,   1,  33, ...,   1,   0,   0],
       [ 65,   3,  69, ...,   1,   0,   0],
       [ 88,  30, 649, ...,   1,   0,   0]])

In [111]:
y = data['Quantity'].to_numpy().reshape(-1,1)

In [112]:
x_train,x_test,y_train,y_test = train_test_split(x,y,test_size = 0.2, random_state = 10)

In [113]:
model = linear_model.LinearRegression()

In [114]:
model.fit(x_train,y_train)

LinearRegression()

In [115]:
dummy.columns

Index(['Unit price', 'Tax 5%', 'Total', 'Rating', 'gross income',
       'DayName_Friday', 'DayName_Monday', 'DayName_Saturday',
       'DayName_Sunday', 'DayName_Thursday', 'DayName_Tuesday',
       'DayName_Wednesday', 'MonthName_February', 'MonthName_January',
       'MonthName_March', 'Branch_A', 'Branch_B', 'Branch_C', 'City_Mandalay',
       'City_Naypyitaw', 'City_Yangon', 'Customer type_Member',
       'Customer type_Normal', 'Gender_Female', 'Gender_Male',
       'Product line_Electronic accessories',
       'Product line_Fashion accessories', 'Product line_Food and beverages',
       'Product line_Health and beauty', 'Product line_Home and lifestyle',
       'Product line_Sports and travel', 'Payment_Cash', 'Payment_Credit card',
       'Payment_Ewallet'],
      dtype='object')

In [116]:
model.coef_

array([[-0.08148571,  0.04516914,  0.0096596 ,  0.04749098,  0.04516914,
        -0.15180136, -0.1191736 ,  0.00532462,  0.02856894,  0.04861556,
         0.13891807,  0.04954778,  0.01193778, -0.01811154,  0.00617376,
         0.01948907,  0.0039432 , -0.02343227,  0.0039432 , -0.02343227,
         0.01948907,  0.05630351, -0.05630351,  0.02377201, -0.02377201,
         0.06531146, -0.0712456 , -0.04873967,  0.02060272, -0.02734965,
         0.06142075,  0.02665938, -0.1155482 ,  0.08888882]])

In [117]:
y_prediction = model.predict(x).astype(int)
y_prediction

array([[ 7],
       [ 5],
       [ 6],
       [ 7],
       [ 7],
       [ 7],
       [ 6],
       [10],
       [ 3],
       [ 3],
       [ 5],
       [ 4],
       [ 5],
       [ 8],
       [10],
       [ 6],
       [ 7],
       [ 5],
       [ 3],
       [ 3],
       [ 4],
       [ 2],
       [ 3],
       [ 5],
       [ 2],
       [ 7],
       [ 3],
       [ 0],
       [ 4],
       [ 6],
       [ 4],
       [ 9],
       [ 8],
       [ 0],
       [ 3],
       [ 1],
       [ 5],
       [ 8],
       [ 7],
       [ 6],
       [ 0],
       [ 2],
       [ 6],
       [ 9],
       [ 4],
       [ 3],
       [ 8],
       [ 6],
       [ 5],
       [10],
       [ 7],
       [ 5],
       [ 5],
       [ 4],
       [ 4],
       [ 8],
       [ 3],
       [ 8],
       [10],
       [ 5],
       [ 4],
       [ 5],
       [ 8],
       [ 6],
       [ 4],
       [ 6],
       [ 3],
       [ 6],
       [10],
       [ 4],
       [11],
       [ 9],
       [ 3],
       [ 6],
       [ 9],
       [ 8],
       [ 8],

In [118]:
data.loc[:, 'prediction'] = y_prediction
data

C:\Users\user\AppData\Local\Temp\ipykernel_14312\2823388792.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Invoice ID   Time    DayName MonthName Branch       City Customer type  \
0    750-67-8428  13:08     Friday   January      A     Yangon        Member   
1    226-31-3081  10:29   Thursday     March      C  Naypyitaw        Normal   
2    631-41-3108  13:23   Saturday     March      A     Yangon        Normal   
3    123-19-1176  20:33   Saturday   January      A     Yangon        Member   
4    373-73-7910  10:37   Thursday  February      A     Yangon        Normal   
5    699-14-3026  18:30     Sunday     March      C  Naypyitaw        Normal   
6    355-53-5943  14:36     Sunday  February      A     Yangon        Member   
7    315-22-5665  11:38   Saturday  February      C  Naypyitaw        Normal   
8    665-32-9167  17:15  Wednesday   January      A     Yangon        Member   
9    692-92-5582  13:27    Tuesday  February      B   Mandalay        Member   
10   351-62-0822  18:07    Tuesday  February      B   Mandalay        Member   
11   529-56-3974  17:03     Friday     March      B   Mandalay        Member   
12   365-64-0515  10:25     Monday  February      A     Yangon        Normal   
13   252-56-2699  16:48  Wednesday  February      A     Yangon        Normal   
14   829-34-3910  19:21   Thursday     March      A     Yangon        Normal   
15   299-46-1805  16:19     Monday   January      B   Mandalay        Member   
16   656-95-9349  11:03     Sunday     March      A     Yangon        Member   
17   765-26-6951  10:39     Monday   January      A     Yangon        Normal   
18   329-62-1586  18:00     Sunday   January      A     Yangon        Normal   
19   319-50-3348  15:30     Sunday     March      B   Mandalay        Normal   
20   300-71-4605  11:24     Sunday  February      C  Naypyitaw        Member   
21   371-85-5789  10:40     Monday     March      B   Mandalay        Normal   
22   273-16-6619  12:20   Thursday     March      B   Mandalay        Normal   
23   636-48-8204  11:15   Saturday  February      A     Yangon        Normal   
24   549-59-1358  17:36     Friday     March      A     Yangon        Member   
25   227-03-5010  19:20   Thursday     March      A     Yangon        Member   
26   649-29-6775  15:31   Thursday  February      B   Mandalay        Normal   
27   189-17-4241  12:17   Saturday     March      A     Yangon        Normal   
28   145-94-9061  19:48   Thursday   January      B   Mandalay        Normal   
29   848-62-7243  15:36   Thursday     March      A     Yangon        Normal   
30   871-79-8483  19:39     Sunday  February      B   Mandalay        Normal   
31   149-71-6266  12:43     Sunday   January      B   Mandalay        Member   
32   640-49-2076  14:49  Wednesday   January      B   Mandalay        Normal   
33   595-11-5460  10:12   Thursday     March      A     Yangon        Normal   
34   183-56-6882  10:42    Tuesday  February      C  Naypyitaw        Member   
35   232-16-2483  12:28     Sunday   January      C  Naypyitaw        Member   
36   129-29-8530  19:15   Saturday     March      A     Yangon        Member   
37   272-65-1806  17:17     Monday   January      A     Yangon        Normal   
38   333-73-7901  13:24     Friday     March      C  Naypyitaw        Normal   
39   777-82-7220  13:01   Saturday     March      B   Mandalay        Member   
40   280-35-5823  18:45  Wednesday   January      B   Mandalay        Member   
41   554-53-8700  10:11     Friday  February      C  Naypyitaw        Member   
42   354-25-5821  13:03   Thursday  February      B   Mandalay        Member   
43   228-96-1411  20:39     Sunday     March      C  Naypyitaw        Member   
44   617-15-4209  19:47     Friday     March      C  Naypyitaw        Member   
45   132-32-9879  18:00     Friday     March      B   Mandalay        Member   
46   370-41-7321  17:24    Tuesday  February      B   Mandalay        Member   
47   727-46-3608  15:47    Tuesday  February      B   Mandalay        Member   
48   669-54-1719  12:45   Saturday  February      B   Mandalay        Member   
49   5

In [119]:
coefficient_determination = r2_score(y,y_prediction)
coefficient_determination

0.7905808219819862

### Ordinary Least Squares Regression Model 

In [139]:
variables_names = ['Unit price', 'Tax 5%', 'Total', 'Rating', 'gross income',
       'DayName_Friday', 'DayName_Monday', 'DayName_Saturday','DayName_Sunday',
       'DayName_Thursday', 'DayName_Tuesday', 'DayName_Wednesday',
       'MonthName_February', 'MonthName_January', 'MonthName_March',
       'Branch_A', 'Branch_B', 'Branch_C', 'City_Mandalay', 'City_Naypyitaw',
       'City_Yangon', 'Customer type_Member', 'Customer type_Normal',
       'Gender_Female', 'Gender_Male', 'Product line_Electronic accessories',
       'Product line_Fashion accessories', 'Product line_Food and beverages',
       'Product line_Health and beauty', 'Product line_Home and lifestyle',
       'Product line_Sports and travel', 'Payment_Cash', 'Payment_Credit card',
       'Payment_Ewallet']

# Add 'constant' to the beginning of your variables_names list
xnames = ['constant'] + variables_names

In [141]:
ols_model = sm.OLS(y_train,sm.add_constant(x_train))
result = ols_model.fit()
result.summary(xname=xnames)


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                      y   R-squared:                       0.819
Model:                            OLS   Adj. R-squared:                  0.814
Method:                 Least Squares   F-statistic:                     152.7
Date:                Mon, 30 Oct 2023   Prob (F-statistic):          1.66e-269
Time:                        12:42:08   Log-Likelihood:                -1316.8
No. Observations:                 800   AIC:                             2682.
Df Residuals:                     776   BIC:                             2794.
Df Model:                          23                                         
Covariance Type:            nonrobust                                         
=======================================================================================================
                                          coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------------------
constant                                1.4441      0.060     23.943      0.000       1.326       1.563
Unit price                             -0.0815      0.002    -36.644      0.000      -0.086      -0.077
Tax 5%                                  0.0452      0.079      0.572      0.567      -0.110       0.200
Total                                   0.0097      0.008      1.283      0.200      -0.005       0.024
Rating                                  0.0475      0.027      1.739      0.082      -0.006       0.101
gross income                            0.0452      0.079      0.572      0.567      -0.110       0.200
DayName_Friday                          0.0545      0.107      0.510      0.610      -0.155       0.264
DayName_Monday                          0.0871      0.108      0.808      0.420      -0.125       0.299
DayName_Saturday                        0.2116      0.114      1.864      0.063      -0.011       0.435
DayName_Sunday                          0.2349      0.117      2.009      0.045       0.005       0.464
DayName_Thursday                        0.2549      0.111      2.296      0.022       0.037       0.473
DayName_Tuesday                         0.3452      0.110      3.127      0.002       0.129       0.562
DayName_Wednesday                       0.2558      0.118      2.165      0.031       0.024       0.488
MonthName_February                      0.4933      0.070      7.039      0.000       0.356       0.631
MonthName_January                       0.4633      0.067      6.867      0.000       0.331       0.596
MonthName_March                         0.4875      0.066      7.413      0.000       0.358       0.617
Branch_A                                0.5009      0.037     13.364      0.000       0.427       0.574
Branch_B                                0.4853      0.037     13.056      0.000       0.412       0.558
Branch_C                                0.4579      0.039     11.684      0.000       0.381       0.535
City_Mandalay                           0.4853      0.037     13.056      0.000       0.412       0.558
City_Naypyitaw                          0.4579      0.039     11.684      0.000       0.381       0.535
City_Yangon                             0.5009      0.037     13.364      0.000       0.427       0.574
Customer type_Member                    0.7784      0.054     14.429      0.000       0.672       0.884
Customer type_Normal                    0.6658      0.056     11.934      0.000       0.556       0.775
Gender_Female                           0.7458      0.054     13.721      0.000       0.639       0.853
Gender_Male                             0.6983      0.055     12.595      0.000       0.589       0.807
Product line_Electronic accessories     0.3060      0.102      2.99

In [143]:
data.to_csv(r"C:/Users/user/Original Sales Predictions.csv")

# Exploratory Data Analysis

In [144]:
df = data
df

Invoice ID   Time    DayName MonthName Branch       City Customer type  \
0    750-67-8428  13:08     Friday   January      A     Yangon        Member   
1    226-31-3081  10:29   Thursday     March      C  Naypyitaw        Normal   
2    631-41-3108  13:23   Saturday     March      A     Yangon        Normal   
3    123-19-1176  20:33   Saturday   January      A     Yangon        Member   
4    373-73-7910  10:37   Thursday  February      A     Yangon        Normal   
5    699-14-3026  18:30     Sunday     March      C  Naypyitaw        Normal   
6    355-53-5943  14:36     Sunday  February      A     Yangon        Member   
7    315-22-5665  11:38   Saturday  February      C  Naypyitaw        Normal   
8    665-32-9167  17:15  Wednesday   January      A     Yangon        Member   
9    692-92-5582  13:27    Tuesday  February      B   Mandalay        Member   
10   351-62-0822  18:07    Tuesday  February      B   Mandalay        Member   
11   529-56-3974  17:03     Friday     March      B   Mandalay        Member   
12   365-64-0515  10:25     Monday  February      A     Yangon        Normal   
13   252-56-2699  16:48  Wednesday  February      A     Yangon        Normal   
14   829-34-3910  19:21   Thursday     March      A     Yangon        Normal   
15   299-46-1805  16:19     Monday   January      B   Mandalay        Member   
16   656-95-9349  11:03     Sunday     March      A     Yangon        Member   
17   765-26-6951  10:39     Monday   January      A     Yangon        Normal   
18   329-62-1586  18:00     Sunday   January      A     Yangon        Normal   
19   319-50-3348  15:30     Sunday     March      B   Mandalay        Normal   
20   300-71-4605  11:24     Sunday  February      C  Naypyitaw        Member   
21   371-85-5789  10:40     Monday     March      B   Mandalay        Normal   
22   273-16-6619  12:20   Thursday     March      B   Mandalay        Normal   
23   636-48-8204  11:15   Saturday  February      A     Yangon        Normal   
24   549-59-1358  17:36     Friday     March      A     Yangon        Member   
25   227-03-5010  19:20   Thursday     March      A     Yangon        Member   
26   649-29-6775  15:31   Thursday  February      B   Mandalay        Normal   
27   189-17-4241  12:17   Saturday     March      A     Yangon        Normal   
28   145-94-9061  19:48   Thursday   January      B   Mandalay        Normal   
29   848-62-7243  15:36   Thursday     March      A     Yangon        Normal   
30   871-79-8483  19:39     Sunday  February      B   Mandalay        Normal   
31   149-71-6266  12:43     Sunday   January      B   Mandalay        Member   
32   640-49-2076  14:49  Wednesday   January      B   Mandalay        Normal   
33   595-11-5460  10:12   Thursday     March      A     Yangon        Normal   
34   183-56-6882  10:42    Tuesday  February      C  Naypyitaw        Member   
35   232-16-2483  12:28     Sunday   January      C  Naypyitaw        Member   
36   129-29-8530  19:15   Saturday     March      A     Yangon        Member   
37   272-65-1806  17:17     Monday   January      A     Yangon        Normal   
38   333-73-7901  13:24     Friday     March      C  Naypyitaw        Normal   
39   777-82-7220  13:01   Saturday     March      B   Mandalay        Member   
40   280-35-5823  18:45  Wednesday   January      B   Mandalay        Member   
41   554-53-8700  10:11     Friday  February      C  Naypyitaw        Member   
42   354-25-5821  13:03   Thursday  February      B   Mandalay        Member   
43   228-96-1411  20:39     Sunday     March      C  Naypyitaw        Member   
44   617-15-4209  19:47     Friday     March      C  Naypyitaw        Member   
45   132-32-9879  18:00     Friday     March      B   Mandalay        Member   
46   370-41-7321  17:24    Tuesday  February      B   Mandalay        Member   
47   727-46-3608  15:47    Tuesday  February      B   Mandalay        Member   
48   669-54-1719  12:45   Saturday  February      B   Mandalay        Member   
49   5

### Best Selling Product

In [152]:
# Calculate Quantity by Product line
sum_sales = df.groupby('Product line')['Total'].sum().reset_index()

# Create a bar chart using Plotly Express
fig = px.bar(sum_sales, x='Product line', y='Total')

# Show the chart
fig.show()

### Best Selling Months 

In [151]:
# Calculate Quantity by Month
sum_sales = df.groupby('MonthName')['Total'].sum().reset_index()

# Create a bar chart using Plotly Express
fig = px.bar(sum_sales, x='MonthName', y='Total')

# Show the chart
fig.show()

### Most used Payment Method 

In [150]:
# Most used payment method 
sum_sales = df.groupby('Payment')['Total'].sum().reset_index()

# Create a bar chart using Plotly Express
fig = px.bar(sum_sales, x='Payment', y='Total')

# Show the chart
fig.show()

### Total sales by customer type 

In [149]:
# Most used payment method 
sum_sales = df.groupby('Customer type')['Total'].sum().reset_index()

# Create a bar chart using Plotly Express
fig = px.bar(sum_sales, x='Customer type', y='Total')

# Show the chart
fig.show()

### Total Sales by Gender 

In [148]:
# Calculate Total by Gender
sum_sales = df.groupby('Gender')['Total'].sum().reset_index()

# Create a bar chart using Plotly Express
fig = px.bar(sum_sales, x='Gender', y='Total')

# Show the chart
fig.show()

### Most Rated Branch

In [147]:
# Calculate mean ratings by branch
mean_ratings = df.groupby('Branch')['Rating'].mean().reset_index()

# Create a bar chart using Plotly Express
fig = px.bar(mean_ratings, x='Branch', y='Rating')

# Show the chart
fig.show()

### Most Patronized Time of the day 

In [146]:
# Calculate Total by Time
sum_sales = df.groupby('Time')['Total'].sum().reset_index()

# Create a bar chart using Plotly Express
fig = px.bar(sum_sales, x='Time', y='Total')

# Show the chart
fig.show()

### Best Selling Day of the Week 

In [145]:
# Calculate Total by Day of the Week
sum_sales = df.groupby('DayName')['Total'].sum().reset_index()

# Create a bar chart using Plotly Express
fig = px.bar(sum_sales, x='DayName', y='Total')

# Show the chart
fig.show()